In [186]:
# Import libraries
import pandas as pd
import numpy as np
import math

from pyspark.sql.functions import col, udf, when

import geopandas
import json

from ipywidgets import interact

from bokeh.io import output_notebook, show, output_file, push_notebook
from bokeh.plotting import figure

from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar, NumeralTickFormatter, ColumnDataSource, HoverTool
from bokeh.palettes import brewer
from bokeh.transform import factor_cmap, jitter

from bokeh.io.doc import curdoc
from bokeh.models import Slider, HoverTool, Select, CustomJS, Div, RangeSlider, Spinner
from bokeh.layouts import row, column, layout

output_notebook()

# from bokeh.io import show
from bokeh.io import show
from bokeh.models import CheckboxGroup, CustomJS
from bokeh.models import AutocompleteInput

Loading BokehJS ...

In [187]:
# Import SparkSession
from pyspark.sql import SparkSession

# Create SparkSession 
spark = SparkSession.builder \
      .master("local[1]") \
      .appName("SparkByExamples.com") \
      .getOrCreate() 

In [188]:
df = pd.read_csv("data/cleaned/all_listings.csv", index_col=["Unnamed: 0"]).dropna()
df=spark.createDataFrame(df)

/home/lynchp/hadoop_dss/spark/python/pyspark/sql/pandas/conversion.py:474: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/home/lynchp/hadoop_dss/spark/python/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


In [189]:
def create_barchart(SparkDF, groupby_columns=['Province', 'County'], value="Price_mean"):
    # Plot a complex chart with interactive hover in a few lines of code
    
    SparkDF_simp = SparkDF.withColumn('County', when(SparkDF.County.startswith('Dublin'), "Dublin").otherwise(SparkDF.County))
    
    df = SparkDF_simp.toPandas()

    group = df.groupby(by=groupby_columns)
    source = ColumnDataSource(group)

    p = figure(width=800, height=400, title=f"Property {value} by {groupby_columns[0]} and {groupby_columns[1]}",
               x_range=group, toolbar_location=None, tools="")

    p.xgrid.grid_line_color = None
    p.xaxis.axis_label = f"{groupby_columns[1]} grouped by {groupby_columns[0]}"
    p.xaxis.major_label_orientation = 1.2
    p.xaxis.major_label_orientation = math.pi/2

    index_cmap = factor_cmap(f'{groupby_columns[0]}_{groupby_columns[1]}', palette=['#2b83ba', '#abdda4', '#ffffbf', '#fdae61', '#d7191c'], 
                             factors=sorted(df.Province.unique()), end=1)

    p.vbar(x=f'{groupby_columns[0]}_{groupby_columns[1]}', top=f"{value}", width=1, source=source,
           line_color="white", fill_color=index_cmap, 
           hover_line_color="darkgrey", hover_fill_color=index_cmap)

    p.add_tools(HoverTool(tooltips=[(f"{value}", f"@{value}"), 
            (f"{groupby_columns[0]}, {groupby_columns[1]}", f'@{groupby_columns[0]}_{groupby_columns[1]}')]))

    return p

In [6]:
pd_df = df.toPandas()

In [190]:
def scatter_plots_price(SparkDF, colName):
    
    df = SparkDF.toPandas()
    df = df[df["Floor_area"] < 2000]
    source = ColumnDataSource(df)
    
    
    if colName != "Floor_area":
        x_range = np.array(sorted(df[colName].unique())).astype(str)
        p = figure(width=800, height=300, x_range=x_range,
                   title=f"Scatterplot of price and {colName}")
        p.circle(y='Price', x=jitter(f'{colName}', width=0.6, range=p.x_range),  source=source, alpha=0.3)
    
    else:
        p = figure(width=800, height=300,
                   title=f"Scatterplot of price and {colName}")
        p.circle(y='Price', x=jitter(f'{colName}', width=0.6),  source=source, alpha=0.3)

    p.x_range.range_padding = 0
    p.ygrid.grid_line_color = None

    return p

In [192]:
#output_file("plot.html")
intro = Div(
    text="""
          <h1>Irish Property Dashboard</h1>
          <p>The data used in the dashboards was scraped from Daft.ie and myhome.ie.</p>
          <p>The dashboard can be broken into two parts.</p>
          <ol>
          <li>Static Nationwide Graphs</li>
          <li>Interactive Graphs</li>
          </ol>
          """,

)
static_dashboards = Div(
    text="""
          <h3>Static Nationwide Graphs</h3>
          <p>The first two graphs illustarte the 
          differences in property price and property 
          sales between counties and provinces in Ireland.
          <br>As you can see Dublin on average is the most expensive,
          but also has the most sales.
          <br>The next three graphs are scatterplots of the features Beds, 
          Baths and Floor area againist the property price. 
          <br>Typically as the number of bedrooms, bathrooms and floor area increases so does the price.</p>
          """,

)

interactive_dashboards = Div(
    text="""
          <h3>Interactive Graphs</h3>
          <p> Enter some data and learn about the property market</p>
          """,

)

complete_price_mean = create_barchart(df, value="Price_mean")
complete_price_count = create_barchart(df, value="Price_count")

sp_beds = scatter_plots_price(df, "Beds")
sp_baths = scatter_plots_price(df, "Baths")
sp_floor_area = scatter_plots_price(df, "Floor_area")

In [193]:
# show the results in a row
show(gridplot([[intro], [static_dashboards], 
[complete_price_mean, complete_price_count], 
[sp_beds, sp_baths],[sp_floor_area],[interactive_dashboards]]))

Start : This command cannot be run due to the error: The system cannot find the file specified.
At line:1 char:1
+ Start "file:///home/lynchp/CA4022/irish_property_analysis/plot2.html"
+ ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
    + CategoryInfo          : InvalidOperation: (:) [Start-Process], InvalidOperationException
    + FullyQualifiedErrorId : InvalidOperationException,Microsoft.PowerShell.Commands.StartProcessCommand
 


In [67]:
pd_df = df.toPandas()

index  Beds  Baths  Floor_area      Price  \
0         2   5.0    3.0       170.0  1100000.0   
1        16   6.0    5.0       595.0  6750000.0   
2        19   5.0    3.0       366.0   750000.0   
3        20   6.0    4.0       360.0   500000.0   
4        38   6.0    3.0       200.0   350000.0   
...     ...   ...    ...         ...        ...   
2135  21293   5.0    2.0       171.0   285000.0   
2136  21306   5.0    5.0       211.7   395000.0   
2137  21314   5.0    3.0       128.0   149000.0   
2138  21317   5.0    3.0       205.0   400000.0   
2139  21319   5.0    3.0       235.0   995000.0   

                                                Address  Property_type  \
0      Lohengrin, 13 Charleville, Churchtown, Dublin 14       Detached   
1          Dungriffan, 2 Sydney Parade Avenue, Dublin 4  Semi-Detached   
2                          Upper, Ballygarvan, Co. Cork       Detached   
3                       Old Road, Cashel, Co. Tipperary       Detached   
4                              Seffin, Birr, Co. Offaly       Detached   
...                                                 ...            ...   
2135                    Damma Lower, Kilkenny, Kilkenny       Detached   
2136   Dun Chaoin, Cor Na Ron East, Inverin, Co. Galway       Detached   
2137            46 Manorview Park, Letterkenny, Donegal  Semi-Detached   
2138                      Naas Road, Kilcullen, Kildare       Detached   
2139   3 Martello Terrace, Strand Road, Bray, Co. Wi...        Terrace   

         County   Province Property_Category  
0     Dublin 14   Leinster             House  
1      Dublin 4   Leinster             House  
2          Cork    Munster             House  
3     Tipperary    Munster             House  
4        Offaly   Leinster             House  
...         ...        ...               ...  
2135   Kilkenny   Leinster             House  
2136     Galway  Connaught             House  
2137    Donegal     Ulster             House  
2138    Kildare   Leinster             House  
2139    Wicklow   Leinster             House  

[2140 rows x 10 columns]

In [180]:
''' An interactivate categorized chart based on a movie dataset.
This example shows the ability of Bokeh to create a dashboard with different
sorting options based on a given dataset.
'''
output_file("plot2.html")
import pandas as pd
from bokeh.io import curdoc
from bokeh.layouts import column, row
from bokeh.models import ColumnDataSource, Div, Select, Slider, TextInput, AutocompleteInput
from bokeh.plotting import figure
from os.path import dirname, join
import pandas.io.sql as psql
import sqlite3 as sql
from sqlalchemy import create_engine
engine = create_engine('sqlite://', echo=False)

desc = Div(text=open("description.html").read(), sizing_mode="stretch_width")
pd_df = pd.read_csv("data/cleaned/all_listings.csv", index_col=["Unnamed: 0"]).dropna()

completion_list = list(pd_df["County"].unique())
sql_df = psql.to_sql(pd_df, 'property', con=engine)

axis_map = {
    "Number of beds": "Beds",
    "Number of baths": "Baths",
    "Size of the property": "Floor_area",
    "Price": "Price",
}

# Create Input controls
min_beds = Slider(title="Minimum number of beds", value=0, start=0, end=20, step=1)
max_beds = Slider(title="Maximum number of beds", value=1, start=1, end=20, step=1)

min_baths = Slider(title="Minimum number of baths", value=0, start=0, end=20, step=1)
max_baths = Slider(title="Maximum number of baths", value=1, start=1, end=20, step=1)

min_price = Slider(title="Minimum price", value=0, start=0, end=10_000_000, step=20000)
max_price = Slider(title="Maximum price", value=100_000, start=100_000, end=10_000_000, step=20000)

min_floor_area = Slider(title="Minimum floor area", value=0, start=0, end=3000, step=100)
max_floor_area = Slider(title="Maximum floor area", value=200, start=200, end=3000, step=100)


counties_slider =  AutocompleteInput(title="Enter a County:", value="All", completions=completion_list)


LABELS = ["House", "Apartment", "Site"]
property_slider =  AutocompleteInput(title="Pick a property category:", value="All", completions=LABELS)


x_axis = Select(title="X Axis", options=sorted(axis_map.keys()), value="Size of the property")
y_axis = Select(title="Y Axis", options=sorted(axis_map.keys()), value="Price")

# Create Column Data Source that will be used by the plot
source = ColumnDataSource(data=dict(x=[], y=[], Price=[], Property_type=[], County=[]))

TOOLTIPS=[
    ("$", "@Price"),
    ("Property_type", "@Property_type"),
    ("County", "@County"),
]

p = figure(height=600, title="", toolbar_location=None, tooltips=TOOLTIPS, sizing_mode="stretch_width")
p.circle(x="x", y="y", source=source, size=7, line_color=None,)


def select_properties():
    
    selected = pd.read_sql_query(
    f'SELECT * FROM property WHERE Beds >= {min_beds.value} AND Beds <= {max_beds.value} AND Baths >= {min_baths.value} AND Baths <= {max_baths.value} AND Price >= {min_price.value} AND Price <= {max_price.value} AND Floor_area >= {min_floor_area.value} AND Floor_area <= {max_floor_area.value}', 
    engine)
    if (counties_slider.value != "All"):
        selected = selected[selected["County"] == counties_slider.value]
    if (property_slider.value != "All"):
        selected = selected[selected["Property_Category"] == property_slider.value]
    return selected.drop(columns=["index"])


def update():
    df = select_properties()
    x_name = axis_map[x_axis.value]
    y_name = axis_map[y_axis.value]
    
    p.xaxis.axis_label = x_axis.value
    p.yaxis.axis_label = y_axis.value
    p.title.text = f"{len(df)} properties selected"
    source.data = dict(
        x=df[x_name],
        y=df[y_name],
        Price=df["Price"],
        Property_type=df["Property_type"],
        County=df["County"],
    )


controls = [min_beds, max_beds, min_baths, max_baths, 
            min_price, max_price, min_floor_area, 
            max_floor_area,counties_slider, property_slider,
            x_axis, y_axis]
for control in controls:
    control.on_change('value', lambda attr, old, new: update())

inputs = column(*controls, width=320, height=800)

layout = column(row(inputs, p, sizing_mode="inherit"), sizing_mode="stretch_width", height=800)

update()  # initial load of the data

curdoc().add_root(layout)
curdoc().title = "Properties"

In [182]:
push_notebook(show(layout))

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html



You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html

Start : This command cannot be run due to the error: The system cannot find the file specified.
At line:1 char:1
+ Start "file:///home/lynchp/CA4022/irish_property_analysis/plot2.html"
+ ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
    + CategoryInfo          : InvalidOperation: (:) [Start-Process], InvalidOperationException
    + FullyQualifiedErrorId : InvalidOperationException,Microsoft.Po

TypeError: push_notebook() takes 0 positional arguments but 1 was given